# Grid Search for Wine Quality Red dataset

In [1]:
# Load required libraries
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.utils.data

import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split

Halving learnig rates after 15.000 iterations.

In [2]:
# Set seed
np.random.seed(1)
torch.manual_seed(1)

# Load Boston Housing dataset
wine_quality = np.genfromtxt('data/winequality-red.csv', delimiter=";")[1:,:]
target = wine_quality[:,-1].reshape(-1,1)
data = wine_quality[:,:-1]

# Split into training, validation and test set
X_train, X_test, y_train, y_test = train_test_split(data, target, test_size=150, random_state=1)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=150, random_state=1)

# Convert arrays to Torch tensors
X_train = torch.FloatTensor(X_train)
y_train = torch.FloatTensor(y_train).view(-1,1)
X_val = torch.FloatTensor(X_val)
y_val = torch.FloatTensor(y_val).view(-1,1)
X_test = torch.FloatTensor(X_test)
y_test = torch.FloatTensor(y_test).view(-1,1)

# Normalise the training dataset
X_train_mean = X_train.mean(0)
X_train_std = X_train.std(0)
X_train_norm = X_train.add(-1, X_train_mean) / X_train_std
y_train_mean = torch.mean(y_train)
y_train_std = torch.std(y_train)
y_train_norm = y_train.add(-1, y_train_mean) / y_train_std

# Define the data-loader
train_data = torch.utils.data.TensorDataset(X_train_norm, y_train_norm)
train_loader = torch.utils.data.DataLoader(train_data, batch_size=32, num_workers=0)
val_data = torch.utils.data.TensorDataset(X_val, y_val)
val_loader = torch.utils.data.DataLoader(val_data, batch_size=150)
test_data = torch.utils.data.TensorDataset(X_test, y_test)
test_loader = torch.utils.data.DataLoader(test_data, batch_size=150)

In [3]:
# Fully connected Feed-Forward network with 2 hidden layers and SELU activations
if torch.cuda.is_available():
    device = torch.device("cuda")
else:
    device = torch.device("cpu")

class Model(nn.Module):

    def __init__(self):
        super(Model, self).__init__()
        self.model = nn.Sequential(
                      nn.Linear(11, 50, bias=True),
                      nn.SELU(),
                      nn.Linear(50, 50, bias=True),
                      nn.SELU(),
                      nn.Linear(50, 50, bias=True),
                      nn.SELU(),
                      nn.Linear(50,1, bias=True)
                    ).to(device)


    def forward(self, x):
        x = x.view(x.size(0), -1)
        x = self.model(x)
        return x

In [4]:
class evaluation(object):
    def __init__(self, test_data, n_samples, X_mean=None, X_std=None, y_mean=None, y_std=None):
        self.test_data = test_data
        self.X_mean = X_mean
        self.X_std = X_std
        self.y_mean = y_mean
        self.y_std = y_std
        self.n = 0
        self.avg_prediction = 0.
        self.sum_pp = 0.
        self.sumsqr_pp = 0.
        self.preds = torch.zeros(len(test_data.dataset),n_samples)

    def fn(self, model):

        with torch.autograd.no_grad():
            self.n += 1
            for x, y in iter(self.test_data):
                x = x.view(x.size(0), -1)

                if (self.X_mean is not None) & (self.X_std is not None):
                    x = (x - self.X_mean).float() / self.X_std

                standard_pred = model(x)

                if (self.y_mean is not None) & (self.y_std is not None):
                    standard_pred = standard_pred * self.y_std + self.y_mean
                
                self.preds[:,self.n-1] = standard_pred.view(-1,)
                self.avg_prediction = self.avg_prediction * (self.n - 1.) / self.n + standard_pred.view(-1,1) / self.n
                self.sum_pp += standard_pred
                self.sumsqr_pp += standard_pred * standard_pred
                std_pred = torch.sqrt((self.sumsqr_pp - (self.sum_pp * self.sum_pp) / self.n) / (self.n - 1))



                norm = torch.distributions.normal.Normal(y, std_pred)
                test_ll = norm.log_prob(self.avg_prediction).mean()



                error = nn.MSELoss(size_average=True)
                rmse = error(self.avg_prediction, y) ** 0.5

                return rmse, test_ll

## SGLD

In [5]:
# Load required libraries
import torch
import torchvision

from torch import nn
import torch.nn.functional as F
import numpy as np

import sgld
import model

# Set seed
np.random.seed(1)
torch.manual_seed(1)


# Network hyperparameters
lambda_ = 1.
# learning_rates = [9e-6, 8e-6, 7e-6, 6e-6, 5e-6, 4e-6, 3e-6, 2e-6, 1e-6, 9e-7, 8e-7]
# learning_rates = [1e-1, 1e-2, 1e-3, 1e-4, 1e-5, 1e-6, 1e-7, 1e-8]
learning_rates = [9e-5, 8e-5, 7e-5, 6e-5, 5e-5, 4e-5, 3e-5, 2e-5, 1e-5, 9e-6, 8e-6, 7e-6, 6e-6, 5e-6, 4e-6, 3e-6, 2e-6, 1e-6]
batch_size = 32.
dataset_size= 1299
# Number of samples to draw from the posterior distribution
n_samples = 300

# Initialise result array
val_llSGLD = np.zeros((1,len(learning_rates)))



for i in range(1):
    for j,lr in enumerate(learning_rates):
        network = Model()
        criterion = nn.MSELoss(size_average=False)
        optim = sgld.optim.sgld(network, lr, lambda_, batch_size, dataset_size)
        evaluate = evaluation(val_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)
        
        t = 1
        n = 0
        for epoch in range(2500):

            running_loss = 0
            for x, y in iter(train_loader):
                x = x.view(x.size(0), -1)

                network.zero_grad()
                output = network(x)
                loss = 0.5 * criterion(output, y)
                loss.backward()
                optim.step()



                running_loss += loss * batch_size / dataset_size

                # Sample from the posterior distribution
                if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                    rmse, val_ll = evaluate.fn(network)
                    n += 1
                t += 1.
            print("lr {:.8f} - epoch {:d} - loss: {:.4f}".format(lr, epoch, running_loss))
        val_llSGLD[i,j] = val_ll

/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))


lr 0.00009000 - epoch 0 - loss: 11.5942
lr 0.00009000 - epoch 1 - loss: 11.6734
lr 0.00009000 - epoch 2 - loss: 11.8026
lr 0.00009000 - epoch 3 - loss: 12.2715
lr 0.00009000 - epoch 4 - loss: 12.1856
lr 0.00009000 - epoch 5 - loss: 12.3521
lr 0.00009000 - epoch 6 - loss: 11.9609


/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


lr 0.00009000 - epoch 7 - loss: 12.4938
lr 0.00009000 - epoch 8 - loss: 12.3891
lr 0.00009000 - epoch 9 - loss: 12.6815
lr 0.00009000 - epoch 10 - loss: 13.2742
lr 0.00009000 - epoch 11 - loss: 12.9683
lr 0.00009000 - epoch 12 - loss: 12.6406
lr 0.00009000 - epoch 13 - loss: 13.1864
lr 0.00009000 - epoch 14 - loss: 14.1514
lr 0.00009000 - epoch 15 - loss: 13.3143
lr 0.00009000 - epoch 16 - loss: 15.4474
lr 0.00009000 - epoch 17 - loss: 14.7248
lr 0.00009000 - epoch 18 - loss: 14.0384
lr 0.00009000 - epoch 19 - loss: 18.0581
lr 0.00009000 - epoch 20 - loss: nan
lr 0.00009000 - epoch 21 - loss: nan
lr 0.00009000 - epoch 22 - loss: nan
lr 0.00009000 - epoch 23 - loss: nan
lr 0.00009000 - epoch 24 - loss: nan
lr 0.00009000 - epoch 25 - loss: nan
lr 0.00009000 - epoch 26 - loss: nan
lr 0.00009000 - epoch 27 - loss: nan
lr 0.00009000 - epoch 28 - loss: nan
lr 0.00009000 - epoch 29 - loss: nan
lr 0.00009000 - epoch 30 - loss: nan
lr 0.00009000 - epoch 31 - loss: nan
lr 0.00009000 - epoch 32 -

lr 0.00009000 - epoch 224 - loss: nan
lr 0.00009000 - epoch 225 - loss: nan
lr 0.00009000 - epoch 226 - loss: nan
lr 0.00009000 - epoch 227 - loss: nan
lr 0.00009000 - epoch 228 - loss: nan
lr 0.00009000 - epoch 229 - loss: nan
lr 0.00009000 - epoch 230 - loss: nan
lr 0.00009000 - epoch 231 - loss: nan
lr 0.00009000 - epoch 232 - loss: nan
lr 0.00009000 - epoch 233 - loss: nan
lr 0.00009000 - epoch 234 - loss: nan
lr 0.00009000 - epoch 235 - loss: nan
lr 0.00009000 - epoch 236 - loss: nan
lr 0.00009000 - epoch 237 - loss: nan
lr 0.00009000 - epoch 238 - loss: nan
lr 0.00009000 - epoch 239 - loss: nan
lr 0.00009000 - epoch 240 - loss: nan
lr 0.00009000 - epoch 241 - loss: nan
lr 0.00009000 - epoch 242 - loss: nan
lr 0.00009000 - epoch 243 - loss: nan
lr 0.00009000 - epoch 244 - loss: nan
lr 0.00009000 - epoch 245 - loss: nan
lr 0.00009000 - epoch 246 - loss: nan
lr 0.00009000 - epoch 247 - loss: nan
lr 0.00009000 - epoch 248 - loss: nan
lr 0.00009000 - epoch 249 - loss: nan
lr 0.0000900

...

lr 0.00000100 - epoch 1558 - loss: 8.7666
lr 0.00000100 - epoch 1559 - loss: 8.7522
lr 0.00000100 - epoch 1560 - loss: 8.7473
lr 0.00000100 - epoch 1561 - loss: 8.7692
lr 0.00000100 - epoch 1562 - loss: 8.7849
lr 0.00000100 - epoch 1563 - loss: 8.7662
lr 0.00000100 - epoch 1564 - loss: 8.7511
lr 0.00000100 - epoch 1565 - loss: 8.7325
lr 0.00000100 - epoch 1566 - loss: 8.7320
lr 0.00000100 - epoch 1567 - loss: 8.7563
lr 0.00000100 - epoch 1568 - loss: 8.7697
lr 0.00000100 - epoch 1569 - loss: 8.7605
lr 0.00000100 - epoch 1570 - loss: 8.7575
lr 0.00000100 - epoch 1571 - loss: 8.7529
lr 0.00000100 - epoch 1572 - loss: 8.7495
lr 0.00000100 - epoch 1573 - loss: 8.7528
lr 0.00000100 - epoch 1574 - loss: 8.7325
lr 0.00000100 - epoch 1575 - loss: 8.7468
lr 0.00000100 - epoch 1576 - loss: 8.7370
lr 0.00000100 - epoch 1577 - loss: 8.7251
lr 0.00000100 - epoch 1578 - loss: 8.7405
lr 0.00000100 - epoch 1579 - loss: 8.7354
lr 0.00000100 - epoch 1580 - loss: 8.7178
lr 0.00000100 - epoch 1581 - loss:

lr 0.00000100 - epoch 1758 - loss: 8.7763
lr 0.00000100 - epoch 1759 - loss: 8.7778
lr 0.00000100 - epoch 1760 - loss: 8.7897
lr 0.00000100 - epoch 1761 - loss: 8.7792
lr 0.00000100 - epoch 1762 - loss: 8.7897
lr 0.00000100 - epoch 1763 - loss: 8.8170
lr 0.00000100 - epoch 1764 - loss: 8.8183
lr 0.00000100 - epoch 1765 - loss: 8.8062
lr 0.00000100 - epoch 1766 - loss: 8.8005
lr 0.00000100 - epoch 1767 - loss: 8.8097
lr 0.00000100 - epoch 1768 - loss: 8.8175
lr 0.00000100 - epoch 1769 - loss: 8.8329
lr 0.00000100 - epoch 1770 - loss: 8.8181
lr 0.00000100 - epoch 1771 - loss: 8.8029
lr 0.00000100 - epoch 1772 - loss: 8.8118
lr 0.00000100 - epoch 1773 - loss: 8.8063
lr 0.00000100 - epoch 1774 - loss: 8.8117
lr 0.00000100 - epoch 1775 - loss: 8.8025
lr 0.00000100 - epoch 1776 - loss: 8.7987
lr 0.00000100 - epoch 1777 - loss: 8.7960
lr 0.00000100 - epoch 1778 - loss: 8.7983
lr 0.00000100 - epoch 1779 - loss: 8.8011
lr 0.00000100 - epoch 1780 - loss: 8.8047
lr 0.00000100 - epoch 1781 - loss:

lr 0.00000100 - epoch 1957 - loss: 8.7276
lr 0.00000100 - epoch 1958 - loss: 8.7285
lr 0.00000100 - epoch 1959 - loss: 8.7284
lr 0.00000100 - epoch 1960 - loss: 8.7191
lr 0.00000100 - epoch 1961 - loss: 8.7112
lr 0.00000100 - epoch 1962 - loss: 8.7425
lr 0.00000100 - epoch 1963 - loss: 8.7289
lr 0.00000100 - epoch 1964 - loss: 8.7210
lr 0.00000100 - epoch 1965 - loss: 8.7370
lr 0.00000100 - epoch 1966 - loss: 8.7352
lr 0.00000100 - epoch 1967 - loss: 8.7585
lr 0.00000100 - epoch 1968 - loss: 8.7630
lr 0.00000100 - epoch 1969 - loss: 8.7547
lr 0.00000100 - epoch 1970 - loss: 8.7696
lr 0.00000100 - epoch 1971 - loss: 8.7507
lr 0.00000100 - epoch 1972 - loss: 8.7315
lr 0.00000100 - epoch 1973 - loss: 8.7342
lr 0.00000100 - epoch 1974 - loss: 8.7331
lr 0.00000100 - epoch 1975 - loss: 8.7266
lr 0.00000100 - epoch 1976 - loss: 8.7183
lr 0.00000100 - epoch 1977 - loss: 8.7191
lr 0.00000100 - epoch 1978 - loss: 8.7301
lr 0.00000100 - epoch 1979 - loss: 8.7363
lr 0.00000100 - epoch 1980 - loss:

lr 0.00000100 - epoch 2153 - loss: 8.5664
lr 0.00000100 - epoch 2154 - loss: 8.5844
lr 0.00000100 - epoch 2155 - loss: 8.5719
lr 0.00000100 - epoch 2156 - loss: 8.5627
lr 0.00000100 - epoch 2157 - loss: 8.5842
lr 0.00000100 - epoch 2158 - loss: 8.6078
lr 0.00000100 - epoch 2159 - loss: 8.6131
lr 0.00000100 - epoch 2160 - loss: 8.6126
lr 0.00000100 - epoch 2161 - loss: 8.6156
lr 0.00000100 - epoch 2162 - loss: 8.6131
lr 0.00000100 - epoch 2163 - loss: 8.6317
lr 0.00000100 - epoch 2164 - loss: 8.6207
lr 0.00000100 - epoch 2165 - loss: 8.6431
lr 0.00000100 - epoch 2166 - loss: 8.6439
lr 0.00000100 - epoch 2167 - loss: 8.6270
lr 0.00000100 - epoch 2168 - loss: 8.6427
lr 0.00000100 - epoch 2169 - loss: 8.6610
lr 0.00000100 - epoch 2170 - loss: 8.6771
lr 0.00000100 - epoch 2171 - loss: 8.6171
lr 0.00000100 - epoch 2172 - loss: 8.6412
lr 0.00000100 - epoch 2173 - loss: 8.6093
lr 0.00000100 - epoch 2174 - loss: 8.5936
lr 0.00000100 - epoch 2175 - loss: 8.6029
lr 0.00000100 - epoch 2176 - loss:

lr 0.00000100 - epoch 2352 - loss: 8.6658
lr 0.00000100 - epoch 2353 - loss: 8.6840
lr 0.00000100 - epoch 2354 - loss: 8.6792
lr 0.00000100 - epoch 2355 - loss: 8.6775
lr 0.00000100 - epoch 2356 - loss: 8.6736
lr 0.00000100 - epoch 2357 - loss: 8.6772
lr 0.00000100 - epoch 2358 - loss: 8.6803
lr 0.00000100 - epoch 2359 - loss: 8.6683
lr 0.00000100 - epoch 2360 - loss: 8.6712
lr 0.00000100 - epoch 2361 - loss: 8.6751
lr 0.00000100 - epoch 2362 - loss: 8.6756
lr 0.00000100 - epoch 2363 - loss: 8.6758
lr 0.00000100 - epoch 2364 - loss: 8.6780
lr 0.00000100 - epoch 2365 - loss: 8.6732
lr 0.00000100 - epoch 2366 - loss: 8.6703
lr 0.00000100 - epoch 2367 - loss: 8.6793
lr 0.00000100 - epoch 2368 - loss: 8.6985
lr 0.00000100 - epoch 2369 - loss: 8.7079
lr 0.00000100 - epoch 2370 - loss: 8.7051
lr 0.00000100 - epoch 2371 - loss: 8.6860
lr 0.00000100 - epoch 2372 - loss: 8.6958
lr 0.00000100 - epoch 2373 - loss: 8.6852
lr 0.00000100 - epoch 2374 - loss: 8.6999
lr 0.00000100 - epoch 2375 - loss:

In [6]:
val_llSGLD
# 3e-5

array([[         nan,          nan,          nan,          nan,
                 nan,          nan,  -0.92538047,  -1.55848825,
         -1.8187921 ,  -1.98701191,  -2.0921886 ,  -2.1076901 ,
         -2.99039578,  -2.43552732,  -3.08332419,  -3.23453975,
         -6.00023985, -15.91482544]])

## pSGLD

In [10]:
import torch
import torchvision
import os

from itertools import chain
from torch import nn
from torchvision import transforms
import torch.nn.functional as F
import numpy as np

import psgld 

np.random.seed(1)
torch.manual_seed(1)





lambda_ = 1.
# learning_rates = [1e-1, 1e-2, 1e-3, 1e-4, 1e-5, 1e-6, 1e-7, 1e-8, 1e-9, 1e-10, 1e-11, 1e-12, 1e-13, 1e-14]
learning_rates = [9e-2, 8e-2, 7e-2, 6e-2, 5e-2, 4e-2, 3e-2, 2e-2, 1e-2, 9e-3, 8e-3, 7e-3, 6e-3, 5e-3, 4e-3, 3e-3, 2e-3, 1e-3]
# learning_rates = [1e-2, 9e-3, 8e-3, 7e-3, 6e-3, 5e-3, 4e-3, 2e-3, 1e-3]
alpha = 0.99


batch_size = 32
dataset_size= 1299

n_chains = 10
n_samples = 300


val_llPSGLD = np.zeros((1,len(learning_rates)))


for i in range(1):
    for j,lr in enumerate(learning_rates):
        network = Model()
        criterion = nn.MSELoss(size_average=False)
        optim = psgld.optim.psgld(network, lr, alpha, lambda_, batch_size, dataset_size)
        evaluate = evaluation(val_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)

        t = 1
        n = 0
        for epoch in range(2500):

            running_loss = 0
            for x, y in iter(train_loader):
                x = x.view(x.size(0), -1)

                network.zero_grad()
                output = network(x)
                loss = 0.5 * criterion(output, y)
                loss.backward()
                optim.step()


                running_loss += loss * batch_size / dataset_size


                if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                    rmse, val_ll = evaluate.fn(network)
                    n += 1
                t += 1.
            print("lr {:.8f} - epoch {:d} - loss: {:.4f}".format(lr, epoch, running_loss))
        val_llPSGLD[i,j] = val_ll

/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))


lr 0.09000000 - epoch 0 - loss: 28329784.0000
lr 0.09000000 - epoch 1 - loss: 84799.9531
lr 0.09000000 - epoch 2 - loss: 53263.7188
lr 0.09000000 - epoch 3 - loss: 41005.5039
lr 0.09000000 - epoch 4 - loss: 36004.8945
lr 0.09000000 - epoch 5 - loss: 30920.5742
lr 0.09000000 - epoch 6 - loss: 27829.3262


/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


lr 0.09000000 - epoch 7 - loss: 44656.6758
lr 0.09000000 - epoch 8 - loss: 13965.7051
lr 0.09000000 - epoch 9 - loss: 11421.8438
lr 0.09000000 - epoch 10 - loss: 11064.2354
lr 0.09000000 - epoch 11 - loss: 12155.5664
lr 0.09000000 - epoch 12 - loss: 15228.5557
lr 0.09000000 - epoch 13 - loss: 8965.1123
lr 0.09000000 - epoch 14 - loss: 13558.6045
lr 0.09000000 - epoch 15 - loss: 18378.0332
lr 0.09000000 - epoch 16 - loss: 10196.9199
lr 0.09000000 - epoch 17 - loss: 5640.2656
lr 0.09000000 - epoch 18 - loss: 8228.7363
lr 0.09000000 - epoch 19 - loss: 10258.8193
lr 0.09000000 - epoch 20 - loss: 5378.1602
lr 0.09000000 - epoch 21 - loss: 2572.3384
lr 0.09000000 - epoch 22 - loss: 2627.4822
lr 0.09000000 - epoch 23 - loss: 11025.2236
lr 0.09000000 - epoch 24 - loss: 1666.3756
lr 0.09000000 - epoch 25 - loss: 749.6827
lr 0.09000000 - epoch 26 - loss: 499.4857
lr 0.09000000 - epoch 27 - loss: 760.8245
lr 0.09000000 - epoch 28 - loss: 571.9750
lr 0.09000000 - epoch 29 - loss: 452.3627
lr 0.090

lr 0.09000000 - epoch 201 - loss: 92.4456
lr 0.09000000 - epoch 202 - loss: 25.3450
lr 0.09000000 - epoch 203 - loss: 18.3566
lr 0.09000000 - epoch 204 - loss: 16.6571
lr 0.09000000 - epoch 205 - loss: 64575.3633
lr 0.09000000 - epoch 206 - loss: 77.1604
lr 0.09000000 - epoch 207 - loss: 4567.3667
lr 0.09000000 - epoch 208 - loss: 281901.6562
lr 0.09000000 - epoch 209 - loss: 940.8008
lr 0.09000000 - epoch 210 - loss: 59558.5078
lr 0.09000000 - epoch 211 - loss: 1178.2067
lr 0.09000000 - epoch 212 - loss: 19.7857
lr 0.09000000 - epoch 213 - loss: 788.7529
lr 0.09000000 - epoch 214 - loss: 16.5275
lr 0.09000000 - epoch 215 - loss: 135393.6250
lr 0.09000000 - epoch 216 - loss: 96.2897
lr 0.09000000 - epoch 217 - loss: 111597.7969
lr 0.09000000 - epoch 218 - loss: 429.4161
lr 0.09000000 - epoch 219 - loss: 76.1435
lr 0.09000000 - epoch 220 - loss: 16.0903
lr 0.09000000 - epoch 221 - loss: 172.4776
lr 0.09000000 - epoch 222 - loss: 115359.5781
lr 0.09000000 - epoch 223 - loss: 598.6926
lr 

...

lr 0.00100000 - epoch 1571 - loss: 55.6954
lr 0.00100000 - epoch 1572 - loss: 49.7654
lr 0.00100000 - epoch 1573 - loss: 47.6926
lr 0.00100000 - epoch 1574 - loss: 42.9186
lr 0.00100000 - epoch 1575 - loss: 40.1269
lr 0.00100000 - epoch 1576 - loss: 37.7267
lr 0.00100000 - epoch 1577 - loss: 37.7558
lr 0.00100000 - epoch 1578 - loss: 35.7487
lr 0.00100000 - epoch 1579 - loss: 34.3832
lr 0.00100000 - epoch 1580 - loss: 31.6814
lr 0.00100000 - epoch 1581 - loss: 31.2984
lr 0.00100000 - epoch 1582 - loss: 29.9377
lr 0.00100000 - epoch 1583 - loss: 28.7364
lr 0.00100000 - epoch 1584 - loss: 28.2815
lr 0.00100000 - epoch 1585 - loss: 28.0805
lr 0.00100000 - epoch 1586 - loss: 27.3211
lr 0.00100000 - epoch 1587 - loss: 26.1610
lr 0.00100000 - epoch 1588 - loss: 26.5035
lr 0.00100000 - epoch 1589 - loss: 26.9899
lr 0.00100000 - epoch 1590 - loss: 26.8750
lr 0.00100000 - epoch 1591 - loss: 24.4789
lr 0.00100000 - epoch 1592 - loss: 25.1662
lr 0.00100000 - epoch 1593 - loss: 24.0148
lr 0.001000

lr 0.00100000 - epoch 1762 - loss: 1458.5599
lr 0.00100000 - epoch 1763 - loss: 1304.8789
lr 0.00100000 - epoch 1764 - loss: 1141.9833
lr 0.00100000 - epoch 1765 - loss: 1021.6596
lr 0.00100000 - epoch 1766 - loss: 917.1389
lr 0.00100000 - epoch 1767 - loss: 831.0377
lr 0.00100000 - epoch 1768 - loss: 755.7894
lr 0.00100000 - epoch 1769 - loss: 685.0013
lr 0.00100000 - epoch 1770 - loss: 967.3204
lr 0.00100000 - epoch 1771 - loss: 826.9542
lr 0.00100000 - epoch 1772 - loss: 738.3368
lr 0.00100000 - epoch 1773 - loss: 668.7096
lr 0.00100000 - epoch 1774 - loss: 613.2744
lr 0.00100000 - epoch 1775 - loss: 566.6623
lr 0.00100000 - epoch 1776 - loss: 522.2333
lr 0.00100000 - epoch 1777 - loss: 481.0701
lr 0.00100000 - epoch 1778 - loss: 445.1685
lr 0.00100000 - epoch 1779 - loss: 412.1951
lr 0.00100000 - epoch 1780 - loss: 380.6812
lr 0.00100000 - epoch 1781 - loss: 350.1161
lr 0.00100000 - epoch 1782 - loss: 323.8065
lr 0.00100000 - epoch 1783 - loss: 301.1973
lr 0.00100000 - epoch 1784 -

lr 0.00100000 - epoch 1952 - loss: 19.2238
lr 0.00100000 - epoch 1953 - loss: 19.6010
lr 0.00100000 - epoch 1954 - loss: 19.5685
lr 0.00100000 - epoch 1955 - loss: 18.8484
lr 0.00100000 - epoch 1956 - loss: 19.1255
lr 0.00100000 - epoch 1957 - loss: 18.9054
lr 0.00100000 - epoch 1958 - loss: 19.0291
lr 0.00100000 - epoch 1959 - loss: 19.1301
lr 0.00100000 - epoch 1960 - loss: 18.9552
lr 0.00100000 - epoch 1961 - loss: 18.5612
lr 0.00100000 - epoch 1962 - loss: 18.8698
lr 0.00100000 - epoch 1963 - loss: 19.4711
lr 0.00100000 - epoch 1964 - loss: 18.5733
lr 0.00100000 - epoch 1965 - loss: 18.4313
lr 0.00100000 - epoch 1966 - loss: 18.3543
lr 0.00100000 - epoch 1967 - loss: 19.6584
lr 0.00100000 - epoch 1968 - loss: 19.0589
lr 0.00100000 - epoch 1969 - loss: 18.7134
lr 0.00100000 - epoch 1970 - loss: 18.5438
lr 0.00100000 - epoch 1971 - loss: 18.2952
lr 0.00100000 - epoch 1972 - loss: 18.5293
lr 0.00100000 - epoch 1973 - loss: 18.2150
lr 0.00100000 - epoch 1974 - loss: 18.4085
lr 0.001000

lr 0.00100000 - epoch 2143 - loss: 14.3155
lr 0.00100000 - epoch 2144 - loss: 14.2782
lr 0.00100000 - epoch 2145 - loss: 14.2254
lr 0.00100000 - epoch 2146 - loss: 14.3472
lr 0.00100000 - epoch 2147 - loss: 14.2640
lr 0.00100000 - epoch 2148 - loss: 14.1156
lr 0.00100000 - epoch 2149 - loss: 14.1008
lr 0.00100000 - epoch 2150 - loss: 14.2967
lr 0.00100000 - epoch 2151 - loss: 14.5930
lr 0.00100000 - epoch 2152 - loss: 14.3781
lr 0.00100000 - epoch 2153 - loss: 14.4543
lr 0.00100000 - epoch 2154 - loss: 14.4869
lr 0.00100000 - epoch 2155 - loss: 15.3925
lr 0.00100000 - epoch 2156 - loss: 14.3588
lr 0.00100000 - epoch 2157 - loss: 14.1079
lr 0.00100000 - epoch 2158 - loss: 14.1615
lr 0.00100000 - epoch 2159 - loss: 14.2693
lr 0.00100000 - epoch 2160 - loss: 14.2285
lr 0.00100000 - epoch 2161 - loss: 14.9463
lr 0.00100000 - epoch 2162 - loss: 14.5429
lr 0.00100000 - epoch 2163 - loss: 14.5062
lr 0.00100000 - epoch 2164 - loss: 15.3735
lr 0.00100000 - epoch 2165 - loss: 14.1197
lr 0.001000

lr 0.00100000 - epoch 2326 - loss: 1100.6282
lr 0.00100000 - epoch 2327 - loss: 1058.7170
lr 0.00100000 - epoch 2328 - loss: 1020.8740
lr 0.00100000 - epoch 2329 - loss: 983.1357
lr 0.00100000 - epoch 2330 - loss: 948.4485
lr 0.00100000 - epoch 2331 - loss: 919.1766
lr 0.00100000 - epoch 2332 - loss: 891.3127
lr 0.00100000 - epoch 2333 - loss: 863.9765
lr 0.00100000 - epoch 2334 - loss: 838.8102
lr 0.00100000 - epoch 2335 - loss: 816.6265
lr 0.00100000 - epoch 2336 - loss: 795.7251
lr 0.00100000 - epoch 2337 - loss: 774.3799
lr 0.00100000 - epoch 2338 - loss: 754.2966
lr 0.00100000 - epoch 2339 - loss: 734.9869
lr 0.00100000 - epoch 2340 - loss: 716.6401
lr 0.00100000 - epoch 2341 - loss: 701.0060
lr 0.00100000 - epoch 2342 - loss: 684.6268
lr 0.00100000 - epoch 2343 - loss: 668.9940
lr 0.00100000 - epoch 2344 - loss: 653.7186
lr 0.00100000 - epoch 2345 - loss: 639.9099
lr 0.00100000 - epoch 2346 - loss: 625.3286
lr 0.00100000 - epoch 2347 - loss: 611.4854
lr 0.00100000 - epoch 2348 - 

In [11]:
val_llPSGLD
#2e-2

array([[-14.83196163, -14.94820023,  -8.98532009,  -9.95477962,
         -7.95416355,  -5.07000017,  -1.47775638,  -0.98914409,
         -2.33380795,  -2.20676684,  -1.49637914,  -2.39978504,
         -2.93608356,  -2.52398944,  -2.91561961,  -1.28630328,
         -2.72300911,  -2.03773165]])

## K-SGLD

In [19]:
import torch
#import torchvision
import os

from itertools import chain
from torch import nn
#from torchvision import transforms
import torch.nn.functional as F
import numpy as np
#from numpy.random import RandomState

import ksgld


np.random.seed(1)
torch.manual_seed(1)



batch_size = 32
dataset_size=1299

n_chains = 10
n_samples = 300



# learning_rates = [1e-4, 1e-5, 1e-6, 1e-7, 1e-8]
#5e-4
#6e-4
#2e-4
#8e-4]
# learning_rates = [1e-3, 9e-4, 8e-4, 7e-4, 6e-4, 5e-4]
learning_rates = [9e-5, 8e-5, 7e-5, 6e-5, 5e-5, 4e-5, 3e-5, 2e-5, 1e-5, 9e-6, 8e-6, 7e-6, 6e-6, 5e-6, 4e-6, 3e-6, 2e-6, 1e-6]


val_llKSGLD = np.zeros((1,len(learning_rates)))


for i in range(1):
    for j,lr in enumerate(learning_rates):
        network = Model()
        criterion = nn.MSELoss(size_average=False)
        optim = ksgld.optim.KSGLD(network, criterion, batch_size, dataset_size, eta=1., v=0., lambda_=1., epsilon=lr, l2=1e-3, invert_every=1)
        evaluate = evaluation(val_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)

        t = 1.
        n = 0


        for epoch in range(2500):
            running_loss = 0
            for x, y in iter(train_loader):
                x = x.view(x.size(0), -1)

                optim.update_curvature(x)

                network.zero_grad()
                output = network(x)
                loss = 0.5 * criterion(output, y)
                loss.backward()
                optim.step()

                running_loss += loss * batch_size / dataset_size

                if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                    rmse, val_ll = evaluate.fn(network)
                    n += 1
                t += 1.
            print("lr {:.8f} - epoch {:d} - loss: {:.4f}".format(lr, epoch, running_loss))
        val_llKSGLD[i,j] = val_ll

/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))
/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='none' instead.
  warnings.warn(warning.format(ret))


lr 0.00009000 - epoch 0 - loss: 13.5607
lr 0.00009000 - epoch 1 - loss: 11.7903
lr 0.00009000 - epoch 2 - loss: 11.4543
lr 0.00009000 - epoch 3 - loss: 11.2594
lr 0.00009000 - epoch 4 - loss: 10.9632
lr 0.00009000 - epoch 5 - loss: 10.7984
lr 0.00009000 - epoch 6 - loss: 10.7256


/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


lr 0.00009000 - epoch 7 - loss: 10.5738
lr 0.00009000 - epoch 8 - loss: 10.4895
lr 0.00009000 - epoch 9 - loss: 10.4519
lr 0.00009000 - epoch 10 - loss: 10.4125
lr 0.00009000 - epoch 11 - loss: 10.2411
lr 0.00009000 - epoch 12 - loss: 10.1787
lr 0.00009000 - epoch 13 - loss: 10.1962
lr 0.00009000 - epoch 14 - loss: 10.1610
lr 0.00009000 - epoch 15 - loss: 10.1313
lr 0.00009000 - epoch 16 - loss: 10.1244
lr 0.00009000 - epoch 17 - loss: 10.1449
lr 0.00009000 - epoch 18 - loss: 10.1874
lr 0.00009000 - epoch 19 - loss: 10.2519
lr 0.00009000 - epoch 20 - loss: 10.0846
lr 0.00009000 - epoch 21 - loss: 10.1720
lr 0.00009000 - epoch 22 - loss: 10.1796
lr 0.00009000 - epoch 23 - loss: 10.0742
lr 0.00009000 - epoch 24 - loss: 10.1001
lr 0.00009000 - epoch 25 - loss: 10.0070
lr 0.00009000 - epoch 26 - loss: 9.9988
lr 0.00009000 - epoch 27 - loss: 9.9955
lr 0.00009000 - epoch 28 - loss: 9.8910
lr 0.00009000 - epoch 29 - loss: 9.9869
lr 0.00009000 - epoch 30 - loss: 9.9924
lr 0.00009000 - epoch 31

lr 0.00009000 - epoch 209 - loss: 9.4415
lr 0.00009000 - epoch 210 - loss: 9.6070
lr 0.00009000 - epoch 211 - loss: 9.0886
lr 0.00009000 - epoch 212 - loss: 9.2698
lr 0.00009000 - epoch 213 - loss: 9.1482
lr 0.00009000 - epoch 214 - loss: 9.2959
lr 0.00009000 - epoch 215 - loss: 9.3355
lr 0.00009000 - epoch 216 - loss: 9.2315
lr 0.00009000 - epoch 217 - loss: 8.8666
lr 0.00009000 - epoch 218 - loss: 9.4944
lr 0.00009000 - epoch 219 - loss: 9.2707
lr 0.00009000 - epoch 220 - loss: 9.4262
lr 0.00009000 - epoch 221 - loss: 9.2013
lr 0.00009000 - epoch 222 - loss: 9.0755
lr 0.00009000 - epoch 223 - loss: 9.0324
lr 0.00009000 - epoch 224 - loss: 9.4194
lr 0.00009000 - epoch 225 - loss: 9.4738
lr 0.00009000 - epoch 226 - loss: 9.2147
lr 0.00009000 - epoch 227 - loss: 9.2471
lr 0.00009000 - epoch 228 - loss: 8.9153
lr 0.00009000 - epoch 229 - loss: 9.4954
lr 0.00009000 - epoch 230 - loss: 9.2575
lr 0.00009000 - epoch 231 - loss: 9.3245
lr 0.00009000 - epoch 232 - loss: 9.1053
lr 0.00009000 - 

...

lr 0.00000100 - epoch 1632 - loss: 2.2285
lr 0.00000100 - epoch 1633 - loss: 2.2274
lr 0.00000100 - epoch 1634 - loss: 2.2275
lr 0.00000100 - epoch 1635 - loss: 2.2290
lr 0.00000100 - epoch 1636 - loss: 2.2294
lr 0.00000100 - epoch 1637 - loss: 2.2283
lr 0.00000100 - epoch 1638 - loss: 2.2286
lr 0.00000100 - epoch 1639 - loss: 2.2256
lr 0.00000100 - epoch 1640 - loss: 2.2284
lr 0.00000100 - epoch 1641 - loss: 2.2270
lr 0.00000100 - epoch 1642 - loss: 2.2279
lr 0.00000100 - epoch 1643 - loss: 2.2288
lr 0.00000100 - epoch 1644 - loss: 2.2286
lr 0.00000100 - epoch 1645 - loss: 2.2291
lr 0.00000100 - epoch 1646 - loss: 2.2250
lr 0.00000100 - epoch 1647 - loss: 2.2247
lr 0.00000100 - epoch 1648 - loss: 2.2249
lr 0.00000100 - epoch 1649 - loss: 2.2253
lr 0.00000100 - epoch 1650 - loss: 2.2275
lr 0.00000100 - epoch 1651 - loss: 2.2271
lr 0.00000100 - epoch 1652 - loss: 2.2286
lr 0.00000100 - epoch 1653 - loss: 2.2271
lr 0.00000100 - epoch 1654 - loss: 2.2258
lr 0.00000100 - epoch 1655 - loss:

lr 0.00000100 - epoch 1828 - loss: 2.1922
lr 0.00000100 - epoch 1829 - loss: 2.1879
lr 0.00000100 - epoch 1830 - loss: 2.1854
lr 0.00000100 - epoch 1831 - loss: 2.1832
lr 0.00000100 - epoch 1832 - loss: 2.1841
lr 0.00000100 - epoch 1833 - loss: 2.1842
lr 0.00000100 - epoch 1834 - loss: 2.1846
lr 0.00000100 - epoch 1835 - loss: 2.1830
lr 0.00000100 - epoch 1836 - loss: 2.1839
lr 0.00000100 - epoch 1837 - loss: 2.1840
lr 0.00000100 - epoch 1838 - loss: 2.1842
lr 0.00000100 - epoch 1839 - loss: 2.1861
lr 0.00000100 - epoch 1840 - loss: 2.1841
lr 0.00000100 - epoch 1841 - loss: 2.1847
lr 0.00000100 - epoch 1842 - loss: 2.1866
lr 0.00000100 - epoch 1843 - loss: 2.1844
lr 0.00000100 - epoch 1844 - loss: 2.1855
lr 0.00000100 - epoch 1845 - loss: 2.1870
lr 0.00000100 - epoch 1846 - loss: 2.1871
lr 0.00000100 - epoch 1847 - loss: 2.1863
lr 0.00000100 - epoch 1848 - loss: 2.1864
lr 0.00000100 - epoch 1849 - loss: 2.1874
lr 0.00000100 - epoch 1850 - loss: 2.1894
lr 0.00000100 - epoch 1851 - loss:

lr 0.00000100 - epoch 2024 - loss: 2.1789
lr 0.00000100 - epoch 2025 - loss: 2.1793
lr 0.00000100 - epoch 2026 - loss: 2.1798
lr 0.00000100 - epoch 2027 - loss: 2.1811
lr 0.00000100 - epoch 2028 - loss: 2.1784
lr 0.00000100 - epoch 2029 - loss: 2.1809
lr 0.00000100 - epoch 2030 - loss: 2.1819
lr 0.00000100 - epoch 2031 - loss: 2.1807
lr 0.00000100 - epoch 2032 - loss: 2.1793
lr 0.00000100 - epoch 2033 - loss: 2.1798
lr 0.00000100 - epoch 2034 - loss: 2.1794
lr 0.00000100 - epoch 2035 - loss: 2.1779
lr 0.00000100 - epoch 2036 - loss: 2.1780
lr 0.00000100 - epoch 2037 - loss: 2.1784
lr 0.00000100 - epoch 2038 - loss: 2.1787
lr 0.00000100 - epoch 2039 - loss: 2.1775
lr 0.00000100 - epoch 2040 - loss: 2.1781
lr 0.00000100 - epoch 2041 - loss: 2.1791
lr 0.00000100 - epoch 2042 - loss: 2.1785
lr 0.00000100 - epoch 2043 - loss: 2.1765
lr 0.00000100 - epoch 2044 - loss: 2.1765
lr 0.00000100 - epoch 2045 - loss: 2.1763
lr 0.00000100 - epoch 2046 - loss: 2.1774
lr 0.00000100 - epoch 2047 - loss:

lr 0.00000100 - epoch 2220 - loss: 2.1499
lr 0.00000100 - epoch 2221 - loss: 2.1510
lr 0.00000100 - epoch 2222 - loss: 2.1500
lr 0.00000100 - epoch 2223 - loss: 2.1502
lr 0.00000100 - epoch 2224 - loss: 2.1509
lr 0.00000100 - epoch 2225 - loss: 2.1502
lr 0.00000100 - epoch 2226 - loss: 2.1516
lr 0.00000100 - epoch 2227 - loss: 2.1518
lr 0.00000100 - epoch 2228 - loss: 2.1516
lr 0.00000100 - epoch 2229 - loss: 2.1505
lr 0.00000100 - epoch 2230 - loss: 2.1501
lr 0.00000100 - epoch 2231 - loss: 2.1511
lr 0.00000100 - epoch 2232 - loss: 2.1504
lr 0.00000100 - epoch 2233 - loss: 2.1510
lr 0.00000100 - epoch 2234 - loss: 2.1521
lr 0.00000100 - epoch 2235 - loss: 2.1511
lr 0.00000100 - epoch 2236 - loss: 2.1519
lr 0.00000100 - epoch 2237 - loss: 2.1515
lr 0.00000100 - epoch 2238 - loss: 2.1505
lr 0.00000100 - epoch 2239 - loss: 2.1513
lr 0.00000100 - epoch 2240 - loss: 2.1509
lr 0.00000100 - epoch 2241 - loss: 2.1505
lr 0.00000100 - epoch 2242 - loss: 2.1515
lr 0.00000100 - epoch 2243 - loss:

lr 0.00000100 - epoch 2417 - loss: 2.1446
lr 0.00000100 - epoch 2418 - loss: 2.1448
lr 0.00000100 - epoch 2419 - loss: 2.1465
lr 0.00000100 - epoch 2420 - loss: 2.1456
lr 0.00000100 - epoch 2421 - loss: 2.1455
lr 0.00000100 - epoch 2422 - loss: 2.1442
lr 0.00000100 - epoch 2423 - loss: 2.1444
lr 0.00000100 - epoch 2424 - loss: 2.1435
lr 0.00000100 - epoch 2425 - loss: 2.1442
lr 0.00000100 - epoch 2426 - loss: 2.1437
lr 0.00000100 - epoch 2427 - loss: 2.1443
lr 0.00000100 - epoch 2428 - loss: 2.1453
lr 0.00000100 - epoch 2429 - loss: 2.1454
lr 0.00000100 - epoch 2430 - loss: 2.1453
lr 0.00000100 - epoch 2431 - loss: 2.1450
lr 0.00000100 - epoch 2432 - loss: 2.1441
lr 0.00000100 - epoch 2433 - loss: 2.1443
lr 0.00000100 - epoch 2434 - loss: 2.1439
lr 0.00000100 - epoch 2435 - loss: 2.1441
lr 0.00000100 - epoch 2436 - loss: 2.1451
lr 0.00000100 - epoch 2437 - loss: 2.1445
lr 0.00000100 - epoch 2438 - loss: 2.1435
lr 0.00000100 - epoch 2439 - loss: 2.1429
lr 0.00000100 - epoch 2440 - loss:

In [20]:
val_llKSGLD
#9e-6

array([[-1.22384417, -1.37941408, -1.20585036, -1.29232454, -1.43980896,
        -1.32352448, -1.13388979, -1.25975418, -1.23479283, -1.11000574,
        -1.19467318, -1.45189607, -1.59301758, -3.01891351, -2.11775088,
        -2.73569345, -5.31936121, -8.70932579]])

## K-SGFS

In [5]:
import torch
#import torchvision
import os

from itertools import chain
from torch import nn
#from torchvision import transforms
import torch.nn.functional as F
import numpy as np
#from numpy.random import RandomState

import ksgfs


np.random.seed(1)
torch.manual_seed(1)



batch_size = 32
dataset_size= 1299

n_chains = 10
n_samples = 300


# learning_rates = [1e-1, 1e-2, 1e-3, 1e-4, 1e-5]
learning_rates = [9e-3, 8e-3, 7e-3, 6e-3, 5e-3, 4e-3, 3e-3, 2e-3, 1e-3, 9e-4, 8e-4, 7e-4, 6e-4, 5e-4, 4e-4, 3e-4, 2e-4, 1e-4]


val_llKSGFS = np.zeros((1,len(learning_rates)))

for i in range(1):
    for j,lr in enumerate(learning_rates):
        network = Model()
        criterion = nn.MSELoss(size_average=False)
        optim = ksgfs.optim.KSGFS(network, criterion, batch_size, dataset_size, eta=1., v=0., lambda_=1., epsilon=lr, l2=1e-3, invert_every=1)
        evaluate = evaluation(val_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)

        t = 1.
        n = 0


        for epoch in range(2500):
            running_loss = 0
            for x, y in iter(train_loader):
                x = x.view(x.size(0), -1)

                optim.update_curvature(x)

                network.zero_grad()
                output = network(x)
                loss = 0.5 * criterion(output, y)
                loss.backward()
                optim.step()

                running_loss += loss * batch_size / dataset_size

                if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                    rmse, val_ll = evaluate.fn(network)
                    n += 1
                t += 1.
            print("lr {:.8f} - epoch {:d} - loss: {:.4f}".format(lr, epoch, running_loss))
#         val_resultsKSGFS[i,j] = rmse
        val_llKSGFS[i,j] = val_ll

/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))
/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='none' instead.
  warnings.warn(warning.format(ret))


lr 0.10000000 - epoch 0 - loss: 12.0901
lr 0.10000000 - epoch 1 - loss: 11.1379
lr 0.10000000 - epoch 2 - loss: 10.7076
lr 0.10000000 - epoch 3 - loss: 10.5102
lr 0.10000000 - epoch 4 - loss: 10.3723
lr 0.10000000 - epoch 5 - loss: 10.2812
lr 0.10000000 - epoch 6 - loss: 10.2474


/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


lr 0.10000000 - epoch 7 - loss: 10.1026
lr 0.10000000 - epoch 8 - loss: 10.0565
lr 0.10000000 - epoch 9 - loss: 10.0667
lr 0.10000000 - epoch 10 - loss: 10.0122
lr 0.10000000 - epoch 11 - loss: 9.9369
lr 0.10000000 - epoch 12 - loss: 9.8889
lr 0.10000000 - epoch 13 - loss: 9.8798
lr 0.10000000 - epoch 14 - loss: 9.8343
lr 0.10000000 - epoch 15 - loss: 9.8203
lr 0.10000000 - epoch 16 - loss: 9.7998
lr 0.10000000 - epoch 17 - loss: 9.8043
lr 0.10000000 - epoch 18 - loss: 9.7685
lr 0.10000000 - epoch 19 - loss: 9.7375
lr 0.10000000 - epoch 20 - loss: 9.6787
lr 0.10000000 - epoch 21 - loss: 9.6794
lr 0.10000000 - epoch 22 - loss: 9.6771
lr 0.10000000 - epoch 23 - loss: 9.6400
lr 0.10000000 - epoch 24 - loss: 9.6357
lr 0.10000000 - epoch 25 - loss: 9.6099
lr 0.10000000 - epoch 26 - loss: 9.6493
lr 0.10000000 - epoch 27 - loss: 9.5253
lr 0.10000000 - epoch 28 - loss: 9.4876
lr 0.10000000 - epoch 29 - loss: 9.4909
lr 0.10000000 - epoch 30 - loss: 9.4761
lr 0.10000000 - epoch 31 - loss: 9.4275

lr 0.10000000 - epoch 210 - loss: 7.4749
lr 0.10000000 - epoch 211 - loss: 7.1104
lr 0.10000000 - epoch 212 - loss: 7.0823
lr 0.10000000 - epoch 213 - loss: 7.0167
lr 0.10000000 - epoch 214 - loss: 7.2776
lr 0.10000000 - epoch 215 - loss: 7.1082
lr 0.10000000 - epoch 216 - loss: 7.0787
lr 0.10000000 - epoch 217 - loss: 6.7318
lr 0.10000000 - epoch 218 - loss: 7.1054
lr 0.10000000 - epoch 219 - loss: 6.9662
lr 0.10000000 - epoch 220 - loss: 6.9582
lr 0.10000000 - epoch 221 - loss: 6.8084
lr 0.10000000 - epoch 222 - loss: 6.7358
lr 0.10000000 - epoch 223 - loss: 6.8916
lr 0.10000000 - epoch 224 - loss: 7.4485
lr 0.10000000 - epoch 225 - loss: 7.0191
lr 0.10000000 - epoch 226 - loss: 6.8751
lr 0.10000000 - epoch 227 - loss: 6.7705
lr 0.10000000 - epoch 228 - loss: 6.8752
lr 0.10000000 - epoch 229 - loss: 7.1065
lr 0.10000000 - epoch 230 - loss: 6.9547
lr 0.10000000 - epoch 231 - loss: 7.0883
lr 0.10000000 - epoch 232 - loss: 6.8921
lr 0.10000000 - epoch 233 - loss: 6.7320
lr 0.10000000 - 

...

lr 0.00001000 - epoch 1680 - loss: 4.6442
lr 0.00001000 - epoch 1681 - loss: 4.6336
lr 0.00001000 - epoch 1682 - loss: 4.6731
lr 0.00001000 - epoch 1683 - loss: 4.6348
lr 0.00001000 - epoch 1684 - loss: 4.6560
lr 0.00001000 - epoch 1685 - loss: 4.6662
lr 0.00001000 - epoch 1686 - loss: 4.6835
lr 0.00001000 - epoch 1687 - loss: 4.6559
lr 0.00001000 - epoch 1688 - loss: 4.6456
lr 0.00001000 - epoch 1689 - loss: 4.6251
lr 0.00001000 - epoch 1690 - loss: 4.6094
lr 0.00001000 - epoch 1691 - loss: 4.6283
lr 0.00001000 - epoch 1692 - loss: 4.6389
lr 0.00001000 - epoch 1693 - loss: 4.6402
lr 0.00001000 - epoch 1694 - loss: 4.6376
lr 0.00001000 - epoch 1695 - loss: 4.6396
lr 0.00001000 - epoch 1696 - loss: 4.6319
lr 0.00001000 - epoch 1697 - loss: 4.6326
lr 0.00001000 - epoch 1698 - loss: 4.6348
lr 0.00001000 - epoch 1699 - loss: 4.6736
lr 0.00001000 - epoch 1700 - loss: 4.6518
lr 0.00001000 - epoch 1701 - loss: 4.6944
lr 0.00001000 - epoch 1702 - loss: 4.6516
lr 0.00001000 - epoch 1703 - loss:

lr 0.00001000 - epoch 1876 - loss: 4.2670
lr 0.00001000 - epoch 1877 - loss: 4.2926
lr 0.00001000 - epoch 1878 - loss: 4.3213
lr 0.00001000 - epoch 1879 - loss: 4.3239
lr 0.00001000 - epoch 1880 - loss: 4.2291
lr 0.00001000 - epoch 1881 - loss: 4.2451
lr 0.00001000 - epoch 1882 - loss: 4.2390
lr 0.00001000 - epoch 1883 - loss: 4.2378
lr 0.00001000 - epoch 1884 - loss: 4.2667
lr 0.00001000 - epoch 1885 - loss: 4.2541
lr 0.00001000 - epoch 1886 - loss: 4.2789
lr 0.00001000 - epoch 1887 - loss: 4.2858
lr 0.00001000 - epoch 1888 - loss: 4.3162
lr 0.00001000 - epoch 1889 - loss: 4.2965
lr 0.00001000 - epoch 1890 - loss: 4.3016
lr 0.00001000 - epoch 1891 - loss: 4.3133
lr 0.00001000 - epoch 1892 - loss: 4.3071
lr 0.00001000 - epoch 1893 - loss: 4.2794
lr 0.00001000 - epoch 1894 - loss: 4.2491
lr 0.00001000 - epoch 1895 - loss: 4.3037
lr 0.00001000 - epoch 1896 - loss: 4.2946
lr 0.00001000 - epoch 1897 - loss: 4.2592
lr 0.00001000 - epoch 1898 - loss: 4.2194
lr 0.00001000 - epoch 1899 - loss:

lr 0.00001000 - epoch 2072 - loss: 3.9361
lr 0.00001000 - epoch 2073 - loss: 3.9033
lr 0.00001000 - epoch 2074 - loss: 3.9228
lr 0.00001000 - epoch 2075 - loss: 3.9101
lr 0.00001000 - epoch 2076 - loss: 3.9503
lr 0.00001000 - epoch 2077 - loss: 3.9243
lr 0.00001000 - epoch 2078 - loss: 3.9652
lr 0.00001000 - epoch 2079 - loss: 3.9382
lr 0.00001000 - epoch 2080 - loss: 3.9019
lr 0.00001000 - epoch 2081 - loss: 3.8967
lr 0.00001000 - epoch 2082 - loss: 3.8895
lr 0.00001000 - epoch 2083 - loss: 3.9045
lr 0.00001000 - epoch 2084 - loss: 3.8858
lr 0.00001000 - epoch 2085 - loss: 3.9002
lr 0.00001000 - epoch 2086 - loss: 3.9341
lr 0.00001000 - epoch 2087 - loss: 3.9146
lr 0.00001000 - epoch 2088 - loss: 3.9342
lr 0.00001000 - epoch 2089 - loss: 3.9447
lr 0.00001000 - epoch 2090 - loss: 3.8716
lr 0.00001000 - epoch 2091 - loss: 3.8693
lr 0.00001000 - epoch 2092 - loss: 3.8860
lr 0.00001000 - epoch 2093 - loss: 3.8986
lr 0.00001000 - epoch 2094 - loss: 3.9134
lr 0.00001000 - epoch 2095 - loss:

lr 0.00001000 - epoch 2268 - loss: 3.7301
lr 0.00001000 - epoch 2269 - loss: 3.7305
lr 0.00001000 - epoch 2270 - loss: 3.6902
lr 0.00001000 - epoch 2271 - loss: 3.6698
lr 0.00001000 - epoch 2272 - loss: 3.6703
lr 0.00001000 - epoch 2273 - loss: 3.6891
lr 0.00001000 - epoch 2274 - loss: 3.7181
lr 0.00001000 - epoch 2275 - loss: 3.7428
lr 0.00001000 - epoch 2276 - loss: 3.6676
lr 0.00001000 - epoch 2277 - loss: 3.6618
lr 0.00001000 - epoch 2278 - loss: 3.6656
lr 0.00001000 - epoch 2279 - loss: 3.6523
lr 0.00001000 - epoch 2280 - loss: 3.6397
lr 0.00001000 - epoch 2281 - loss: 3.6608
lr 0.00001000 - epoch 2282 - loss: 3.6661
lr 0.00001000 - epoch 2283 - loss: 3.6384
lr 0.00001000 - epoch 2284 - loss: 3.6784
lr 0.00001000 - epoch 2285 - loss: 3.6111
lr 0.00001000 - epoch 2286 - loss: 3.6629
lr 0.00001000 - epoch 2287 - loss: 3.6729
lr 0.00001000 - epoch 2288 - loss: 3.6937
lr 0.00001000 - epoch 2289 - loss: 3.6899
lr 0.00001000 - epoch 2290 - loss: 3.7048
lr 0.00001000 - epoch 2291 - loss:

lr 0.00001000 - epoch 2464 - loss: 3.5392
lr 0.00001000 - epoch 2465 - loss: 3.5314
lr 0.00001000 - epoch 2466 - loss: 3.5807
lr 0.00001000 - epoch 2467 - loss: 3.5705
lr 0.00001000 - epoch 2468 - loss: 3.5570
lr 0.00001000 - epoch 2469 - loss: 3.5565
lr 0.00001000 - epoch 2470 - loss: 3.5347
lr 0.00001000 - epoch 2471 - loss: 3.5279
lr 0.00001000 - epoch 2472 - loss: 3.5691
lr 0.00001000 - epoch 2473 - loss: 3.5250
lr 0.00001000 - epoch 2474 - loss: 3.5640
lr 0.00001000 - epoch 2475 - loss: 3.5387
lr 0.00001000 - epoch 2476 - loss: 3.5367
lr 0.00001000 - epoch 2477 - loss: 3.5617
lr 0.00001000 - epoch 2478 - loss: 3.5361
lr 0.00001000 - epoch 2479 - loss: 3.5306
lr 0.00001000 - epoch 2480 - loss: 3.5025
lr 0.00001000 - epoch 2481 - loss: 3.5236
lr 0.00001000 - epoch 2482 - loss: 3.5265
lr 0.00001000 - epoch 2483 - loss: 3.5272
lr 0.00001000 - epoch 2484 - loss: 3.5109
lr 0.00001000 - epoch 2485 - loss: 3.5255
lr 0.00001000 - epoch 2486 - loss: 3.5313
lr 0.00001000 - epoch 2487 - loss:

In [6]:
val_llKSGFS
# 1e-3

array([[ -1.4129765 ,  -1.79684734,  -0.96114969,  -2.16377068,
        -24.82130241]])